In [1]:
import torch
torch.__version__

'2.1.0+cu121'

In [2]:
!nvcc --version

nvcc: NVIDIA (R) Cuda compiler driver
Copyright (c) 2005-2023 NVIDIA Corporation
Built on Mon_Apr__3_17:16:06_PDT_2023
Cuda compilation tools, release 12.1, V12.1.105
Build cuda_12.1.r12.1/compiler.32688072_0


In [3]:
import xformers
xformers.__version__

'0.0.22.post7'

In [4]:
!python -m bitsandbytes

++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++
++++++++++++++++++ BUG REPORT INFORMATION ++++++++++++++++++
++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++
++++++++++++++++++++++++++ OTHER +++++++++++++++++++++++++++
CUDA specs: CUDASpecs(highest_compute_capability=(8, 9), cuda_version_string='121', cuda_version_tuple=(12, 1))
PyTorch settings found: CUDA_VERSION=121, Highest Compute Capability: (8, 9).
To manually override the PyTorch CUDA version please see: https://github.com/TimDettmers/bitsandbytes/blob/main/docs/source/nonpytorchcuda.mdx
The directory listed in your path is found to be non-existent: /usr/local/nvidia/lib
The directory listed in your path is found to be non-existent: /usr/local/nvidia/lib64
The directory listed in your path is found to be non-existent: /workspace/Untitled.ipynb
The directory listed in your path is found to be non-existent: //matplotlib_inline.backend_inline
CUDA SETUP: WARNING! CUDA runtime files not found in any environ

In [5]:
from unsloth import FastLanguageModel
from transformers import AutoTokenizer

max_seq_length = 2048
load_in_4bit = True
dtype = None

revision = "63ea4c7c4f4cae078655294c96973d0db75cd656"
pretrained_model_hf = "Finnish-NLP/Ahma-3B"

model, _ = FastLanguageModel.from_pretrained(
    model_name = pretrained_model_hf,
    max_seq_length = max_seq_length,
    dtype = torch.bfloat16,
    load_in_4bit = load_in_4bit,
    revision = revision
)

🦥 Unsloth: Will patch your computer to enable 2x faster free finetuning.


config.json:   0%|          | 0.00/662 [00:00<?, ?B/s]

==((====))==  Unsloth: Fast Llama patching release 2024.6
   \\   /|    GPU: NVIDIA GeForce RTX 4090. Max memory: 23.65 GB. Platform = Linux.
O^O/ \_/ \    Pytorch: 2.1.0+cu121. CUDA = 8.9. CUDA Toolkit = 12.1.
\        /    Bfloat16 = TRUE. Xformers = 0.0.22.post7. FA = True.
 "-____-"     Free Apache license: http://github.com/unslothai/unsloth


model.safetensors.index.json:   0%|          | 0.00/19.5k [00:00<?, ?B/s]

model-00001-of-00002.safetensors:   0%|          | 0.00/4.95G [00:00<?, ?B/s]

...

generation_config.json:   0%|          | 0.00/116 [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/2.90k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/4.84M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/414 [00:00<?, ?B/s]

Finnish-NLP/Ahma-3B does not have a padding token! Will use pad_token = <unk>.


In [6]:
tokenizer = AutoTokenizer.from_pretrained(pretrained_model_hf, revision=revision)

In [8]:
tokenizer.clean_up_tokenization_spaces = True
tokenizer.add_tokens(["<PAD>"])
tokenizer.pad_token = "<PAD>"
tokenizer.add_eos_token = False

model.resize_token_embeddings(new_num_tokens=len(tokenizer))
model.config.eos_token_id = tokenizer.eos_token_id

In [10]:
model = FastLanguageModel.get_peft_model(
    model,
    target_modules = ["q_proj", "k_proj", "v_proj", "o_proj",
                      "gate_proj", "up_proj", "down_proj"],
    modules_to_save = ["lm_head", "embed_tokens"],
    lora_alpha = 16,
    r = 32,
    lora_dropout = 0,
    bias = "none",
    use_gradient_checkpointing="unsloth",
    random_state=3407,
    use_rslora = True,
    loftq_config = None,
    max_seq_length = max_seq_length
)
    

Unsloth: Offloading input_embeddings to disk to save VRAM
Unsloth: Offloading output_embeddings to disk to save VRAM


Unsloth 2024.6 patched 26 layers with 26 QKV layers, 26 O layers and 26 MLP layers.


Unsloth: Casting embed_tokens to float32
Unsloth: Casting lm_head to float32


In [11]:
from datasets import load_dataset

dataset = load_dataset("intfloat/multilingual_cc_news", languages=["fi"])["train"]
print(f'Dataset contains: {len(dataset)} articles')

The repository for intfloat/multilingual_cc_news contains custom code which must be executed to correctly load the dataset. You can inspect the repository content at https://hf.co/datasets/intfloat/multilingual_cc_news.
You can avoid this prompt in future by passing the argument `trust_remote_code=True`.

Do you wish to run the custom code? [y/N]  y


Generating train split: 0 examples [00:00, ? examples/s]

Dataset contains: 1536679 articles


In [12]:
dataset

Dataset({
    features: ['title', 'maintext', 'url', 'date_publish'],
    num_rows: 1536679
})

In [13]:
print(f'Articles title:\n{dataset[0]["title"]}')
print('-' * 50)
print(f'Articles title:\n{dataset[0]["maintext"]}')

Articles title:
Postin tulisi kiinnostua myös tuoreista lehdistä
--------------------------------------------------
Articles title:
Posti kertoi eilen tiedotteessaan, että sen työntekijät siirtyvät tällä viikolla nurmikonleikkuusta lehtien haravoimiseen. Postin verkkokaupasta ja Postin omista myymälöistä voi tilata pihan haravoinnin haluamilleen kahdelle tiistaipäivälle. Syyslehdille voi myös tilata Postilta poisviennin.
Samaan aikaan, kun postin varsinaista palvelutehtävää — postilähetysten kuljettamista asiakkailleen — on heikennetty, valtionyhtiö tekee kaikkensa tunkeutuakseen yksityisten yritysten tonteille kiinteistönhoito- ja sosiaalitöihin.
Syksyn putoavien lehtien sijasta Postin tulisi keskittää tarmonsa siihen, miten se hoitaa tuoreiden lehtien eli paikallis- , sanoma- ja aikakauslehtien kuljetuksen. Tienoo tosin on hankkinut varhaiskantopalvelunsa yksityiseltä toimijalta, mutta Posti vie tai sen pitäisi viedä ydinaluetta kauempana oleville tilaajille lehdet määräaikoina. Käyt

In [14]:
dataset_filtered = dataset.select([i for i in range(3000)])

dataset_filtered = dataset_filtered.rename_column('maintext', 'instruction')
dataset_filtered = dataset_filtered.rename_column('title', 'response')

In [16]:
def form_instruction(row):
  row["instruction"] = f'Saat seuraavana artikkelin tekstin. Tehtävänäsi on tuottaa otsikko artikkelin perusteella.\n Artikkeli:\n{row["instruction"]}\n Nyt luo otsikko artikkelin perusteella. \n Otsikko: \n'
  return row

dataset_filtered = dataset_filtered.map(form_instruction)

Map:   0%|          | 0/3000 [00:00<?, ? examples/s]

In [19]:
def form_messages(row):
    row["messages"] = [{'role': 'user', 'content': row["instruction"]}, {'role': 'assistant', 'content': row["response"]}]
    return row

dataset_filtered = dataset_filtered.map(form_messages)

Map:   0%|          | 0/3000 [00:00<?, ? examples/s]

In [22]:
def form_prompt(row):
    row["text"] = tokenizer.apply_chat_template(row["messages"], tokenize=False)
    return row

dataset_filtered = dataset_filtered.map(form_prompt)

Map:   0%|          | 0/3000 [00:00<?, ? examples/s]

In [23]:
dataset_filtered[0]

{'response': 'Postin tulisi kiinnostua myös tuoreista lehdistä',
 'instruction': 'Saat seuraavana artikkelin tekstin. Tehtävänäsi on tuottaa otsikko artikkelin perusteella.\n Artikkeli:\nPosti kertoi eilen tiedotteessaan, että sen työntekijät siirtyvät tällä viikolla nurmikonleikkuusta lehtien haravoimiseen. Postin verkkokaupasta ja Postin omista myymälöistä voi tilata pihan haravoinnin haluamilleen kahdelle tiistaipäivälle. Syyslehdille voi myös tilata Postilta poisviennin.\nSamaan aikaan, kun postin varsinaista palvelutehtävää — postilähetysten kuljettamista asiakkailleen — on heikennetty, valtionyhtiö tekee kaikkensa tunkeutuakseen yksityisten yritysten tonteille kiinteistönhoito- ja sosiaalitöihin.\nSyksyn putoavien lehtien sijasta Postin tulisi keskittää tarmonsa siihen, miten se hoitaa tuoreiden lehtien eli paikallis- , sanoma- ja aikakauslehtien kuljetuksen. Tienoo tosin on hankkinut varhaiskantopalvelunsa yksityiseltä toimijalta, mutta Posti vie tai sen pitäisi viedä ydinaluett

In [24]:
from unsloth import UnslothTrainer, UnslothTrainingArguments
import math

batch_size = 4
eval_batch_size = 4
gradient_accumulation_steps = 4
epochs = 1
train_steps = math.ceil(len(dataset_filtered) / batch_size / gradient_accumulation_steps * epochs)
eval_steps = math.floor(train_steps/epochs/5)
warmup_steps = math.ceil(train_steps * 0.1)
dataset_split = dataset_filtered.train_test_split(test_size=0.05)
output_dir = 'train_checkpoints'

In [25]:
trainer = UnslothTrainer(
    model = model,
    tokenizer = tokenizer,
    train_dataset = dataset_split["train"],
    eval_dataset = dataset_split["test"],
    dataset_text_field = 'text',
    max_seq_length = max_seq_length,
    dataset_num_proc = 2,
    packing=False,
    args = UnslothTrainingArguments(
        per_device_train_batch_size = batch_size,
        per_device_eval_batch_size = eval_batch_size,
        gradient_accumulation_steps = gradient_accumulation_steps,
        warmup_steps = warmup_steps,
        max_steps = train_steps,
        eval_steps = eval_steps,
        save_steps = eval_steps,
        evaluation_strategy = 'steps',
        save_strategy = 'steps',
        learning_rate = 0.00002,
        fp16=False,
        bf16=True,
        logging_steps=5,
        optim = "paged_adamw_8bit",
        weight_decay = 0.005,
        lr_scheduler_type = 'cosine',
        seed=3407,
        output_dir = output_dir
    ),
)
        

/usr/local/lib/python3.10/dist-packages/transformers/training_args.py:1474: FutureWarning: `evaluation_strategy` is deprecated and will be removed in version 4.46 of 🤗 Transformers. Use `eval_strategy` instead
  warnings.warn(


Map (num_proc=2):   0%|          | 0/2850 [00:00<?, ? examples/s]

Map (num_proc=2):   0%|          | 0/150 [00:00<?, ? examples/s]

max_steps is given, it will override any value given in num_train_epochs


In [26]:
trainer.train()

==((====))==  Unsloth - 2x faster free finetuning | Num GPUs = 1
   \\   /|    Num examples = 2,850 | Num Epochs = 2
O^O/ \_/ \    Batch size per device = 4 | Gradient Accumulation steps = 4
\        /    Total batch size = 16 | Total steps = 188
 "-____-"     Number of trainable parameters = 462,096,640


/usr/local/lib/python3.10/dist-packages/peft/utils/save_and_load.py:209: UserWarning: Setting `save_embedding_layers` to `True` as the embedding layer has been resized during finetuning.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/peft/utils/save_and_load.py:209: UserWarning: Setting `save_embedding_layers` to `True` as the embedding layer has been resized during finetuning.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/peft/utils/save_and_load.py:209: UserWarning: Setting `save_embedding_layers` to `True` as the embedding layer has been resized during finetuning.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/peft/utils/save_and_load.py:209: UserWarning: Setting `save_embedding_layers` to `True` as the embedding layer has been resized during finetuning.
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/peft/utils/save_and_load.py:209: UserWarning: Setting `save_embedding_layers` to `True` as the embedding layer has been resized during finetunin

TrainOutput(global_step=188, training_loss=1.9880720529150455, metrics={'train_runtime': 754.5522, 'train_samples_per_second': 3.986, 'train_steps_per_second': 0.249, 'total_flos': 5.843729764618752e+16, 'train_loss': 1.9880720529150455, 'epoch': 1.0546984572230014})

In [ ]:
from transfomers import GenerationConfig

generation_config = GenerationConfig(
    pad_token_id = tokenizer.pad_token_id,
    eos_token_id = tokenizer.convert_tokens_to_ids("</s>")
)

In [37]:
len(dataset_split["test"])

150

In [52]:
import random
i = random.randint(0, len(dataset_split["test"]))

model.eval()

inputs = tokenizer([tokenizer.apply_chat_template([{'role': 'user', 'content': dataset_split["test"][i]["instruction"]}], tokenize=False)] * 1, return_tensors='pt').to("cuda")

with torch.no_grad():
    generation_ids = model.generate(
        input_ids = inputs["input_ids"],
        attention_mask = inputs["attention_mask"],
        generation_config = generation_config, **{
            "temperature": 0.7,
            "penalty_alpha": 0.6,
            "min_p": 0.5,
            "do_sample": True,
            "repetition_penalty": 1.28,
            "min_length": 6,
            "max_new_tokens": 50})

generated_text = tokenizer.batch_decode(generation_ids, skip_special_tokens = False, cleanup_tokenization_spaces = True)[0]
print('--------')
print(generated_text)
            

--------
<s><s> [INST] <<SYS>>
Olet tekoälyavustaja. Vastaat aina mahdollisimman avuliaasti. Vastauksesi eivät saa sisältää mitään haitallista, epäeettistä, rasistista, seksististä, vaarallista tai laitonta sisältöä. Jos kysymyksessä ei ole mitään järkeä tai se ei ole asiasisällöltään johdonmukainen, selitä miksi sen sijaan, että vastaisit jotain väärin. Jos et tiedä vastausta kysymykseen, älä kerro väärää tietoa.
<</SYS>>

Saat seuraavana artikkelin tekstin. Tehtävänäsi on tuottaa otsikko artikkelin perusteella.
 Artikkeli:
Tiedekeskus Heurekan Pokémon Go -päivä keräsi lauantaina paikalle järjestäjien laskujen mukaan noin 2 000 pelaajaa. Päivään kuului paitsi pelaamista, myös tutkijoiden luentoja pelaamisesta ja lisätystä todellisuudesta.
”Lisätty todellisuus on kiinnostava ilmiö, ja nyt kun tällainen hyvin sosiaalinen peli on noussut pinnalle, halusimme tuoda aiheeseen tieteellisen näkökulman”, kertoo Heurekan tapahtumatuottaja Siina Vasama.
”Paikalla oli teiniporukoita, paljon perhe